# Hyper parameter search for TD3+BC

In [1]:
!pip install d3rlpy

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import math
import subprocess
import os
import d3rlpy
# plt.style.use('matplotlibrc')

# from Python.data_sampler import *

## Building an MDPDataset

We first read in a large batch of samples from the file. As `d3rlpy` wants it in the form (observations, actions, rewards, terminal flags), we go ahead and do that. Here's a helper function to get a dataset from a list of chunks of your choosing.

In [3]:
import numpy as np
import torch
import random
import pandas
from Python.data_sampler import *

In [4]:
def get_dataset(chunks : list, batch_size=30000, 
                path="collected_data/rl_det_small.txt") -> d3rlpy.dataset.MDPDataset :
    random.seed(0)
    samples = DataSampler(path_to_data=path)
    samples.setting("coarse")
    states = []
    actions = []
    rewards = []
    next_states = []
    for chunk in chunks:
        samples.use_chunk(chunk)
        samples.read_chunk()
        [statesChunk, actionsChunk, rewardsChunk, nextStatesChunk] = samples.get_batch(batch_size)
        states.append(statesChunk)
        actions.append(actionsChunk)
        rewards.append(rewardsChunk)
        next_states.append(nextStatesChunk)
    states = torch.cat(states)
    actions = torch.cat(actions)
    rewards = torch.cat(rewards)
    next_states = torch.cat(next_states)
    terminals = np.zeros(len(states))
    terminals[::1111] = 1 #episode length 100, change if necessary
    print(states.shape)
    dataset = d3rlpy.dataset.MDPDataset(states.numpy(), 
                                        actions.numpy(), 
                                        rewards.numpy(), terminals)
    return dataset, states.numpy(), actions.numpy(), rewards.numpy()

We can build the dataset from there, just like this, and split into train and test sets.

In [5]:
dataset, states, actions, rewards = get_dataset([i for  i in range(100)], path="collected_data/rl_stochpid.txt")

start
[ 0.00000000e+00  7.95731469e+08 -4.75891077e-02 -3.69999953e-02
  2.00999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.50429671e-01 -4.92727243e-01 -5.31666025e-03]
Read chunk # 1 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  3.25610892e-01 -3.35999953e-02
 -2.42000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -3.08749986e-01  6.00000000e-01 -6.00000000e-01]
Read chunk # 2 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.90489108e-01 -5.87999953e-02
 -1.01000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.76979602e-02 -6.00000000e-01  6.00000000e-01]
Read chunk # 3 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  4.48010892e-01  4.64000047e-02
 -1.04000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -4.83151637e-01  6.00000000e-01 -6.00000000e-01]
Read chunk # 4 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.08389108e-01  3.32000047e-02
 -2.02000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -4.25137655

[ 0.00000000e+00  7.95731469e+08  4.45610892e-01 -4.15999953e-02
 -1.45000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -4.82854667e-01  6.00000000e-01 -6.00000000e-01]
Read chunk # 51 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  3.36410892e-01 -3.37999953e-02
  8.49998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.45025378e-01  1.67203680e-01 -6.00000000e-01]
Read chunk # 52 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.02189108e-01 -2.81999953e-02
  1.33999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.85653844e-01 -2.69594451e-01  6.00000000e-01]
Read chunk # 53 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.06389108e-01 -5.79999531e-03
 -2.02000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.00000000e-01 -3.87850514e-02  6.00000000e-01]
Read chunk # 54 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -6.79891077e-02 -1.81999953e-02
  2.77999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-

torch.Size([111000, 6])


In [6]:
print("The behavior policy value statistics are:")
dataset.compute_stats()['return']

The behavior policy value statistics are:


{'mean': -136.20181,
 'std': 106.013954,
 'min': -410.7058,
 'max': 0.0,
 'histogram': (array([ 4,  1,  4,  2,  1,  0,  3,  2,  5,  2,  0,  2,  6,  5,  8, 13, 12,
         28,  1,  1]),
  array([-410.7058  , -390.17053 , -369.63522 , -349.09995 , -328.56464 ,
         -308.02936 , -287.49408 , -266.95877 , -246.4235  , -225.8882  ,
         -205.3529  , -184.81761 , -164.28232 , -143.74704 , -123.21175 ,
         -102.67645 ,  -82.14116 ,  -61.605873,  -41.07058 ,  -20.53529 ,
            0.      ], dtype=float32))}

In [7]:
from sklearn.model_selection import train_test_split
train_episodes, test_episodes = train_test_split(dataset, test_size=0.2)

## Setting up an Algorithm

In [8]:
from d3rlpy.algos import CQL, TD3PlusBC
from d3rlpy.models.encoders import VectorEncoderFactory

from d3rlpy.preprocessing import MinMaxActionScaler
import random
action_scaler = MinMaxActionScaler(minimum=-0.6, maximum=0.6)

from d3rlpy.metrics.scorer import td_error_scorer
from d3rlpy.metrics.scorer import average_value_estimation_scorer
from d3rlpy.metrics.scorer import initial_state_value_estimation_scorer

from d3rlpy.ope import FQE
# metrics to evaluate with
from d3rlpy.metrics.scorer import soft_opc_scorer
import pickle as pkl
from statistics import harmonic_mean as hm

## Perform a random search on hyper params. 

As good fqe on both stochastic and deterministic data is needed for good performance during the evaluation step in the simulator, we take the harmonic mean of both fqes to understand the performance on each dataset. The harmonic mean is large only when each number whose mean is being taken is large. Therefore, a large harmonic mean corresponds to large numbers whose mean is being taken.


In [9]:

# The number of times we would wanna do a random search for hyper-params. In 
# every random search, we randomly pick a new set of hyper-params.
num_search_iterations = 40
largest_fqe = -np.inf

for i in range(num_search_iterations):

    random.seed()

    actor_lr_this_iter = random.uniform(1e-5, 1e-2)
    critic_lr_this_iter = random.uniform(1e-5, 1e-2)
    temp_lr_this_iter = random.uniform(1e-5, 1e-4)
    n_steps_this_iter = random.choice([1, 3, 5, 7])

    actor_encoder = VectorEncoderFactory(hidden_units=[12, 24, 36, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)
    critic_encoder = VectorEncoderFactory(hidden_units=[12, 24, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)

    print("search iteration: ", i)
    print("using hyper params: ", [actor_lr_this_iter, critic_lr_this_iter, 
                                   temp_lr_this_iter, n_steps_this_iter])

    model = TD3PlusBC(q_func_factory='qr', #qr -> quantile regression q function, but you don't have to use this
                reward_scaler='standard',
                actor_encoder_factory = actor_encoder,
                critic_encoder_factory = critic_encoder,
                action_scaler=action_scaler,
                actor_learning_rate=actor_lr_this_iter, 
                critic_learning_rate=critic_lr_this_iter,
                n_steps=n_steps_this_iter, 
                use_gpu=True) #change it to true if you have one
    model.build_with_dataset(dataset)

    model.fit(train_episodes,
        eval_episodes=test_episodes,
        n_epochs=50, 
        tensorboard_dir='runs',
        scorers={
            'td_error': td_error_scorer,
            'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+100 for i  in range(20)], 
                                                                    path="collected_data/rl_stochpid.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_stoch = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+200 for i in range(40)], 
                                                                    path="collected_data/rl_purestochastic.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_det = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    if(hm([history_stoch[-1][1]["ave_value"] + 50, 
           history_det[-1][1]["ave_value"] + 50]) \
                                                          > largest_fqe):
        largest_fqe = hm([history_stoch[-1][1]["ave_value"] + 50, 
                         history_det[-1][1]["ave_value"] + 50])

        # Save the hyper-params
        hyperparams = [actor_lr_this_iter, critic_lr_this_iter, 
                       temp_lr_this_iter, n_steps_this_iter]

        with open("hyperparams_td3bc.pkl", "wb") as f:
            print("most optimal hyper params for td3+bc at this point: ", hyperparams)
            pkl.dump(hyperparams, f)

        # Save model and policy
        model.save_model("model_hyperparams_td3bc.pt")
        model.save_policy("policy_hyperparams_td3bc.pt")


search iteration:  0
using hyper params:  [0.009031438021208704, 0.009411437505950367, 5.849528243704872e-05, 5]
2022-04-18 20:53.30 [debug    ] RoundIterator is selected.
2022-04-18 20:53.30 [info     ] Directory is created at d3rlpy_logs/TD3PlusBC_20220418205330
2022-04-18 20:53.30 [debug    ] Fitting scaler...              scaler=standard
2022-04-18 20:53.30 [debug    ] Fitting action scaler...       action_scaler=min_max
2022-04-18 20:53.30 [debug    ] Fitting reward scaler...       reward_scaler=standard
2022-04-18 20:53.30 [warning  ] Skip building models since they're already built.
2022-04-18 20:53.30 [info     ] Parameters are saved to d3rlpy_logs/TD3PlusBC_20220418205330/params.json params={'action_scaler': {'type': 'min_max', 'params': {'minimum': array(-0.6), 'maximum': array(0.6)}}, 'actor_encoder_factory': {'type': 'vector', 'params': {'hidden_units': [12, 24, 36, 24, 12], 'activation': 'relu', 'use_batch_norm': True, 'dropout_rate': 0.2, 'use_dense': False}}, 'actor_lear

Epoch 1/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-18 20:53.33 [info     ] TD3PlusBC_20220418205330: epoch=1 step=342 epoch=1 metrics={'time_sample_batch': 0.00026271008608634013, 'time_algorithm_update': 0.007491200290925321, 'critic_loss': 38.940454438415884, 'actor_loss': 2.6343131438333387, 'time_step': 0.007802201990495648, 'td_error': 0.9401714699769707, 'init_value': -5.584756374359131, 'ave_value': -2.6096547902103615} step=342
2022-04-18 20:53.33 [info     ] Model parameters are saved to d3rlpy_logs/TD3PlusBC_20220418205330/model_342.pt


Epoch 2/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-18 20:53.36 [info     ] TD3PlusBC_20220418205330: epoch=2 step=684 epoch=2 metrics={'time_sample_batch': 0.0002588124303092733, 'time_algorithm_update': 0.006231283583836249, 'critic_loss': 44.24783430601421, 'actor_loss': 2.581866677044428, 'time_step': 0.006537937978554887, 'td_error': 1.215804687550027, 'init_value': -8.151300430297852, 'ave_value': -4.18715050070169} step=684
2022-04-18 20:53.36 [info     ] Model parameters are saved to d3rlpy_logs/TD3PlusBC_20220418205330/model_684.pt


...

2022-04-19 00:31.46 [info     ] FQE_20220419003011: epoch=49 step=17395 epoch=49 metrics={'time_sample_batch': 0.00010251394459899043, 'time_algorithm_update': 0.005075245843806737, 'loss': 0.5341114191023607, 'time_step': 0.005219143880924708, 'init_value': -15.966272354125977, 'ave_value': -15.92169359388307, 'soft_opc': nan} step=17395


2022-04-19 00:31.46 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220419003011/model_17395.pt


Epoch 50/50:   0%|          | 0/355 [00:00<?, ?it/s]

2022-04-19 00:31.48 [info     ] FQE_20220419003011: epoch=50 step=17750 epoch=50 metrics={'time_sample_batch': 0.00010433465662136884, 'time_algorithm_update': 0.0050111710185736, 'loss': 0.5279196474753635, 'time_step': 0.0051572201957165355, 'init_value': -16.018083572387695, 'ave_value': -16.038061470575773, 'soft_opc': nan} step=17750


2022-04-19 00:31.48 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220419003011/model_17750.pt


## Reading hyper params from file

In [10]:
with open("hyperparams_td3bc.pkl", "rb") as f:
    data = pkl.load(f)

print(data)

[0.004343795776698955, 3.716957428808228e-05, 1.1126761324425686e-05, 3]
